In [ ]:
#FASTQC and trimming info here: http://onsnetwork.org/kubu4/2018/05/16/trimgalorefastqcmultiqc-trimgalore-rrbs-geoduck-bs-seq-fastq-data-directional/

In [ ]:
!mkdir /Volumes/web/metacarcinus/Pgenerosa/GENOMES

In [ ]:
!mkdir /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070

In [3]:
!mkdir /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/Bismark_genome

In [ ]:
#copy Pgenerosa genome v070 to metacarcinus folder to build genome

In [ ]:
!cp /Volumes/web-1/halfshell/genomic-databank/Pgenerosa_v070.fa /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070

In [ ]:
#move to the directory where we want to save the genome

In [1]:
!cd /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070

In [ ]:
#build Bismark genome using ostrich

In [ ]:
!/Users/Shared/bioinformatics/bismark_v0.15.0/bismark_genome_preparation \
--path_to_bowtie /Users/Shared/bioinformatics/bowtie2-2.2.9//bowtie2 \
--verbose /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070 \
2> /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/genomeprep.err

In [ ]:
#genomeprep.err says "Warning: Encountered reference sequence with only gaps"

In [ ]:
#Checking .fa file for gaps and missing sequence (http://seqanswers.com/forums/showthread.php?t=6301)

In [ ]:
#first make short file with only the chromosome and the first line of sequence

In [ ]:
!grep '>'  -A 1 /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/Pgenerosa_v070.fa \
> /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/missing_seq_check

In [ ]:
#then check for chromosomes where there is no sequence (based on this code:  https://www.biostars.org/p/78786/)

In [2]:
!awk 'BEGIN {RS = ">" ; FS = "\n" ; ORS = ""} {if (!$2) print ">"$0}' \
/Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/missing_seq_check

>

In [ ]:
#doesn't seem to be any chromosomes where sequence is missing 
#not sure why the carrot printed out
#running another check in case there is a line with no chromosome name

In [3]:
!grep '>$' /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/missing_seq_check

In [ ]:
#confirmed there are no chromosomes without any sequence or random carrots
#now testing for NNNNs in seqeuence

In [5]:
!grep NNNN /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/Pgenerosa_v070.fa |head

GNNNNNNNNNNAACTGTTACACAATGCATCATCCGAGGATCTTTTGTAATAATAAGTATCACCCTCCTGACTCAGACCAA
TTTTTTCTCCCACCCGGAATGTTTTCTATCCCCTTCCCCCCCNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNN
NNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNCAAACAGCATGGGAACAA
TACATTAGGAACTTTGCTATAAAGGACAGTAAGATAATTGACAAAAATGTACAGATGTATACTTAAAAGTNNNNNNNNNN
NNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNN
NNNNNNNNNNGACATGTTCCCTACTGTCATTTCCAGATCTGTGAGACATGTTCCCTAATGTCATTTCCATCATTGTGAGA
ACCGGTAGAGGGTACTGCATAGAATAATGTTCAGAATATATATANNNNNNNNNNGATACCGGTAGAGGGTACTGCATAGA
TTGCATAGGAGACTAGACAGAAGATTTTTTTTTTCGATCTGAAATTCAAGATGGCCGCCATTACTAAAAATNNNNNNNNN
NNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNNN
NNNNNNNNNNNATGTAAATGATTTTGCCTATATCTTCACAGAAGCATTGTTTGGTGAAGGAGGTTCAGATTTGTAAAAAT
^C


In [ ]:
#lots of lines contain many Ns. Is this problematic? No, see Explore Geoduck mapping #415 (https://github.com/RobertsLab/resources/issues/415)

In [ ]:
#test alignments using subset of data. 
#Ran 20181011_bmrkAS1.2I60test_Pgenr.sh on mox which aligned 10K reads per sample
#transferred everything from gscratch on mox to Gannet
#rsync --archive --progress --verbose strigg@mox.hyak.uw.edu:/gscratch/srlab/strigg/analyses/20181011 .

In [ ]:
#report mapping efficiency and genome coverage

In [4]:
#create summary report of mapping efficiency and dedup. 
!cat /Volumes/web/metacarcinus/Pgenerosa/20181011/*PE_report.txt | \
grep 'Mapping\ efficiency\:' | \
cat - /Volumes/web/metacarcinus/Pgenerosa/20181011/*.deduplication_report.txt | \
grep 'Mapping\ efficiency\:\|removed' \
> /Volumes/web/metacarcinus/Pgenerosa/20181011/EPI_mapping_dedup_summary.txt

In [ ]:
##compiling bam files and sorting

In [7]:
%%bash
find /Volumes/web/metacarcinus/Pgenerosa/20181011/*deduplicated.bam| \
xargs basename -s _R1_001_val_1_bismark_bt2_pe.deduplicated.bam | xargs -I{} /Users/Shelly/anaconda3/bin/samtools \
sort /Volumes/web/metacarcinus/Pgenerosa/20181011/{}_R1_001_val_1_bismark_bt2_pe.deduplicated.bam \
-o /Volumes/web/metacarcinus/Pgenerosa/20181011/{}_dedup.sorted.bam


In [ ]:
## create methylation extractor files for estimating coverage. 
## got command from Steven's notebook (https://github.com/sr320/nb-2018/blob/master/O_lurida/07-Bismark-wgbs.ipynb)

In [ ]:
%%bash
/Users/Shared/bioinformatics/bismark_v0.15.0/bismark_methylation_extractor \
--paired-end --bedGraph --counts --scaffolds \
--multicore 2 \
/Volumes/web/metacarcinus/Pgenerosa/20181011/*deduplicated.bam \
-o /Volumes/web/metacarcinus/Pgenerosa/20181011/ \
--samtools /usr/local/bin/samtools \
2> /Volumes/web/metacarcinus/Pgenerosa/20181011/bme.err

In [ ]:
#make summary report 
#need to install latestversion of bismark because 0.15.0 doesn't ahve summary option


In [6]:
!conda install -c bioconda bismark

Solving environment: done

## Package Plan ##

  environment location: /Users/strigg/anaconda3

  added / updated specs: 
    - bismark


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    psutil-5.4.7               |   py36h1de35cc_0         314 KB
    decorator-4.3.0            |           py36_0          15 KB
    parso-0.3.1                |           py36_0         114 KB
    partd-0.3.9                |           py36_0          32 KB
    pylint-2.1.1               |           py36_0         795 KB
    datashape-0.5.4            |           py36_1         100 KB
    pep8-1.7.1                 |           py36_0          51 KB
    qtawesome-0.5.1            |           py36_1         569 KB
    unicodecsv-0.14.1          |   py36he531d66_0          25 KB
    conda-build-3.10.9         |           py36_0         433 KB
    pycparser-2.19             |           py36_0         173 KB
   

    pathlib2:                           2.3.2-py37_0                     --> 2.3.2-py36_0                    
    patsy:                              0.5.0-py37_0                     --> 0.5.0-py36_0                    
    pep8:                               1.7.1-py37_0                     --> 1.7.1-py36_0                    
    pexpect:                            4.6.0-py37_0                     --> 4.6.0-py36_0                    
    pickleshare:                        0.7.4-py37_0                     --> 0.7.5-py36_0                    
    pillow:                             5.2.0-py37hb68e598_0             --> 5.3.0-py36hb68e598_0            
    pip:                                10.0.1-py37_0                    --> 10.0.1-py36_0                   
    pkginfo:                            1.4.2-py37_1                     --> 1.4.2-py36_1                    
    pluggy:                             0.7.1-py37h28b3542_0             --> 0.8.0-py36_0                    
    ply:  

Proceed ([y]/n)? ^C

CondaSystemExit: 
Operation aborted.  Exiting. 



In [ ]:
#make individual reports before making whole summary

In [9]:
%%bash
cd /Volumes/web/metacarcinus/Pgenerosa/20181011/
/Users/strigg/anaconda3/bin/bismark2report

In [10]:
%%bash
cd /Volumes/web/metacarcinus/Pgenerosa/20181011/
/Users/strigg/anaconda3/bin/bismark2summary 



In [2]:
##organize files 
!mkdir /Volumes/web/metacarcinus/Pgenerosa/20181011/OG_bams
!mkdir /Volumes/web/metacarcinus/Pgenerosa/20181011/dedup_bams
!mkdir /Volumes/web/metacarcinus/Pgenerosa/20181011/dedup_sorted_bams
!mkdir /Volumes/web/metacarcinus/Pgenerosa/20181011/BisMeExt
!mkdir /Volumes/web/metacarcinus/Pgenerosa/20181011/reports
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/*_pe.bam /Volumes/web/metacarcinus/Pgenerosa/20181011/OG_bams
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/*.deduplicated.bam /Volumes/web/metacarcinus/Pgenerosa/20181011/dedup_bams
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/*.sorted.bam /Volumes/web/metacarcinus/Pgenerosa/20181011/dedup_sorted_bams
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/*.gz /Volumes/web/metacarcinus/Pgenerosa/20181011/BisMeExt
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/*report.txt /Volumes/web/metacarcinus/Pgenerosa/20181011/reports

In [3]:
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/bme.err /Volumes/web/metacarcinus/Pgenerosa/20181011/BisMeExt/
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/dedup.err /Volumes/web/metacarcinus/Pgenerosa/20181011/dedup_bams/
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/*.merged /Volumes/web/metacarcinus/Pgenerosa/20181011/BisMeExt/
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/*.M-bias.txt /Volumes/web/metacarcinus/Pgenerosa/20181011/BisMeExt/

In [4]:
!mv /Volumes/web/metacarcinus/Pgenerosa/20181011/*.deduplicated.txt /Volumes/web/metacarcinus/Pgenerosa/20181011/BisMeExt/

In [ ]:
##Test to see if 'Chromosomal sequence could not be extracted' issue persists with padded genome as suggested by Felix: 
#https://github.com/FelixKrueger/Bismark/issues/94
#First make padded genome

In [ ]:
!awk '{if($1~/>/)print "&"$1"&";else print $1}' \
/Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/Pgenerosa_v070.fa | \
tr '\n' '@' | tr -d '@' | tr '&' '\n' | \
awk 'NR>1{if($1!~/>/)print "NN"$1"NN";else print $1}'  \
> /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/padded/Pgenerosa_v070_padded.fa

In [ ]:
#build Bismakr genome with padded fasta; ENDED UP RUNNING THIS ON MOX

In [ ]:
!/Users/strigg/anaconda3/bin/bismark_genome_preparation \
--path_to_bowtie /Users/strigg/anaconda3/bin/ \
--verbose /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/padded/ \
2> /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/padded/genomeprep.err

In [ ]:
#try running alignment with subset of one sample

In [ ]:
!/Users/strigg/anaconda3/bin/bismark \
--path_to_bowtie /Users/strigg/anaconda3/bin/ \
--samtools_path /Users/strigg/anaconda3/bin/ \
--score_min L,0,-1.2 \
-I 60 \
-p 8 \
--genome /Volumes/web/metacarcinus/Pgenerosa/GENOMES/v070/padded \
-1 /Volumes/web-1/Athaliana/20180516_geoduck_trimgalore_rrbs/EPI-103_S27_L005_R1_001_val_1.fq.gz \
-2 /Volumes/web-1/Athaliana/20180516_geoduck_trimgalore_rrbs/EPI-103_S27_L005_R2_001_val_2.fq.gz  \
-o /Volumes/web/metacarcinus/Pgenerosa/20181101